
# Plot SUVI L2 Coronal Hole Boundaries
Purpose:
  Use Python to plot the SUVI L2 coronal hole boundary (chbnd) product in various coordinate systems.


## Overview



In this example, we will be plotting the coronal hole boundaries (chbnd_loc) from
the coronal hole boundary product. The boundaries are determined by outlining the coronal hole classifications from
the SUVI Thematic Map algorithm.

We will plot chbnd_loc for each of the following coordinate systems:
 * Heliographic Stonyhurst `(longitude, latitude)`
 * Heliographic Carrington `(longitude, latitude)`
 * Pixel `(x pixels, y pixels)`
 * Helioprojective Cartesian `(x arcsec, y arcsec)`
 * Heliocentric Cartesian `(x AU, y AU, z AU)`
 * Heliocentric Radial `(solar radii, degrees, z solar radii)`

`Note for this product: The extent is only available in the Heliographic Stonyhurst coordinate system.`



## Imports



First, we will import the necessary libraries:



In [ ]:
__authors__ = "elucas, ajarvis"

import matplotlib.pyplot as plt
import matplotlib.cm as cm
import numpy as np
from datetime import datetime, timedelta
import netCDF4 as nc
from astropy.coordinates import SkyCoord
import sunpy
import sunpy.map
import astropy.units as u
from sunpy.coordinates import frames
from sunpy.net import Fido, attrs as a
from astropy.io import fits

## Helper Functions
We need to define a few helper functions for use throughout plotting:



In [ ]:
# Fetch the SUVI SunPy map to use as a base for plotting.
def create_suvi_sunpymap(date, goes=16, wavelength=131, rng=2):
    ds0 = (date - timedelta(minutes=rng)).strftime("%Y/%m/%d %H:%M:%S")
    ds1 = (date + timedelta(minutes=rng)).strftime("%Y/%m/%d %H:%M:%S")
    q = Fido.search(a.Time(ds0, ds1), a.Instrument.suvi, a.Wavelength(wavelength*u.angstrom))
    tmp_files = Fido.fetch(q)
    # Select only files for level 2 composites from G16
    for tmp_file in tmp_files:
        if (f'g{goes}' in tmp_file) and ('l2' in tmp_file):
            data, header = fits.getdata(tmp_file, ext=1), fits.getheader(tmp_file, ext=1)
            suvi_map = sunpy.map.Map(data, header)
            return suvi_map, data, header
    print('No SUVI map available')
    return None

In [ ]:
# Convert time given in the .nc file to datetime.
def convert_time(time_nc):
    date_2000 = datetime(2000, 1, 1, 12, 0)
    date = date_2000 + timedelta(seconds=time_nc)
    return date

In [ ]:
# Define legend for this product.
def legend_handles(coord=''):
    markers = ['o']
    fillstyle = ['full']
    labels = ['chbnd_loc']
    if coord == 'hg':
        markers += ['_']
        fillstyle += ['full']
        labels += ['chbnd_extent']
    f = lambda m, fill: plt.plot([], [], marker=m, color='k', ls='-', fillstyle=fill)[0]
    handles = [f(markers[i], fillstyle[i]) for i in range(len(markers))]
    return handles, labels

## Retrieving the SUVI SunPy Map



| Let's use some of the helper functions above to retrieve a SUVI image.
| We'll grab an image of the sun in the 195Å wavelength for datetime 2024-09-12 23:28.
| Example data file: [dr_suvi-l2-chbnd_g16_s20240912T232800Z_e20240912T233200Z_v1-0-6.nc](../../_static/suvi/dr_suvi-l2-chbnd_g16_s20240912T232800Z_e20240912T233200Z_v1-0-6.nc)_



In [ ]:
date = datetime(2024, 9, 12, 23, 28)
goes = 16
wavelength = 195
suvi_chbnd_path = f'../../data/suvi/dr_suvi-l2-chbnd_g16_s20240912T232800Z_e20240912T233200Z_v1-0-6.nc'
chbnd_nc = nc.Dataset(suvi_chbnd_path)

Let's look at the variables contained in the coronal hole boundary files.



In [ ]:
for k in chbnd_nc.variables.keys():
    print(k)

For our examples, we will be looking at the chbnd_loc variable.
We can see the general structure by inspecting this variable in any coordinate system, for example,
in Heliographic Stonyhurst.



In [ ]:
print(chbnd_nc['chbnd_loc_hg'])

| The structure in this example is `(1, 4, 16, 2)`:
|  `1` : The first dimension of the structure is the time dimension, which will always have 1 value for this product.
|  `4` : The second dimension is the number of separate coronal holes within this image.
|  `16`: The third dimension is each vertex of the coronal hole boundary polygon. We are limited to 16 vertices for legacy operational reasons.
|  `2` : The fourth dimension is the coordinate pair (3 for HCC and HCR) of each vertex, with units as described above.



We need to extract the time (found in the 'time' variable), and convert to python datetime in order to fetch a
corresponding SUVI SunPy map at the closest time possible.



In [ ]:
# Get file time
chbnd_time = convert_time(chbnd_nc['time'][:][0])
# Access SUVI SunPy map for that time and defined wavelength
suvi_map, suvi_data, suvi_header = create_suvi_sunpymap(chbnd_time, goes=goes, wavelength=wavelength)

## Plotting the Coronal Holes
Now that the SUVI SunPy map has been retrieved, we can overplot the coordinates from the .nc file onto that image.

`Note: Heliographic Stonyhurst and Heliographic Carrington are only defined on-disk, so any features
(or pieces of features) that extend off-disk will not be plotted.`



### Heliographic Stonyhurst Coordinates



In [ ]:
# Plot the composite image
fig_hgs = plt.figure(figsize=(10, 10))
fig_hgs.tight_layout(h_pad=-50)
fig_hgs.suptitle(f'Heliographic Stonyhurst Coordinates, GOES-{goes}')
ax_hgs = fig_hgs.add_subplot(projection=suvi_map)
suvi_map.plot(axes=ax_hgs, clip_interval=(0.1, 99.9) * u.percent)

# Ignore INFO message about 'Missing metadata for solar radius: assuming the standard radius of the photosphere.'
# RSUN_REF will be included in future data products.

chbnd_hg = chbnd_nc['chbnd_loc_hg'][:].data[0]

colors = cm.Reds_r(np.linspace(0.3, 0.6, len(chbnd_hg)))

for hole, c in zip(chbnd_hg, colors):
    hole = [*hole, hole[0]]
    hole = np.array(hole, dtype=float)
    hole = np.where(hole == -9999., np.nan, hole)
    chbnd_hgs_sc = SkyCoord([(float(v[0]), float(v[1])) * u.degree for v in hole], obstime=date,
                            observer=suvi_map.observer_coordinate, frame=frames.HeliographicStonyhurst)

    # Transform skycoord object to the suvi sunpy map's coordinate frame
    chbnd_hgs_sc.transform_to(suvi_map.coordinate_frame)

    # Plot flare
    ax_hgs.plot_coord(chbnd_hgs_sc, color=c, marker='o', markersize=2)

chbnd_extent = chbnd_nc['chbnd_extent_hg'][:].data[0]

for hole, c in zip(chbnd_extent, colors):
    hole = np.array(hole, dtype=float)
    hole = np.where(hole == -9999., np.nan, hole)
    if np.isnan(hole).all():
        continue

    # coordinates are in N(0) lat, S(1) lat, E(2) lon, W(3) lon
    # (lon, lat) because skycoord is in (lon, lat)
    bl_coord = [hole[2], hole[1]]
    tr_coord = [hole[3], hole[0]]

    bottom_left = SkyCoord(bl_coord[0] * u.degree, bl_coord[1] * u.degree, obstime=date,
                           observer=suvi_map.observer_coordinate, frame=frames.HeliographicStonyhurst)
    top_right = SkyCoord(tr_coord[0] * u.degree, tr_coord[1] * u.degree, obstime=date,
                         observer=suvi_map.observer_coordinate, frame=frames.HeliographicStonyhurst)

    suvi_map.draw_quadrangle(bottom_left, top_right=top_right, axes=ax_hgs,
                             edgecolor=c, linewidth=1)

# Add legend for features
handles, labels = legend_handles(coord='hg')
plt.legend(handles, labels, loc=1, framealpha=1)

plt.show()

### Heliographic Carrington Coordinates



In [ ]:
# Plot the SUVI SunPy composite image
fig_car = plt.figure(figsize=(10, 10))
fig_car.tight_layout(h_pad=-50)
fig_car.suptitle(f'Heliographic Carrington Coordinates, GOES-{goes}')
ax_car = fig_car.add_subplot(projection=suvi_map)
suvi_map.plot(axes=ax_car, clip_interval=(0.1, 99.9) * u.percent)

# Extract coronal hole boundary array from netCDF
chbnd_car = chbnd_nc['chbnd_loc_car'][:].data[0]
colors = cm.YlOrBr_r(np.linspace(0.3, 0.6, len(chbnd_car)))

for hole, c in zip(chbnd_car, colors):
    hole[hole == -9999.] = np.nan
    # Close boundary polygon
    hole = [*hole, hole[0]]

    chbnd_car_sc = SkyCoord([(float(v[0]), float(v[1])) * u.degree for v in hole], obstime=date,
                            observer=suvi_map.observer_coordinate, frame=frames.HeliographicCarrington)
    # Transform SkyCoord object to the SUVI SunPy map's coordinate frame
    chbnd_car_sc = chbnd_car_sc.transform_to(suvi_map.coordinate_frame)

    # Plot boundary
    ax_car.plot_coord(chbnd_car_sc, color=c, marker='o', markersize=2)

# Add legend for features
handles, labels = legend_handles()
plt.legend(handles, labels, loc=1, framealpha=1)

plt.show()

### Pixel Coordinates



In [ ]:
# Plot the SUVI SunPy composite image
fig_px = plt.figure(figsize=(10, 10))
fig_px.tight_layout()
ax_px = fig_px.add_subplot(projection=suvi_map)
suvi_map.plot(axes=ax_px, clip_interval=(0.1, 99.9) * u.percent)
fig_px.suptitle(f'Pixel Coordinates, GOES-{goes}')

# Extract coronal hole boundary array from netCDF
chbnd_pix = chbnd_nc['chbnd_loc_pix'][:].data[0]
colors = cm.Greens_r(np.linspace(0.3, 0.6, len(chbnd_pix)))

for hole, c in zip(chbnd_pix, colors):
    hole[hole == -9999.] = np.nan
    # Close boundary polygon
    hole = [*hole, hole[0]]

    chbnd_pix_x = [h[0] for h in hole]
    chbnd_pix_y = [h[1] for h in hole]

    # Plot boundary
    ax_px.plot_coord(chbnd_pix_x, chbnd_pix_y, color=c, marker='o', markersize=2)

# Add legend for features
handles, labels = legend_handles()
plt.legend(handles, labels, loc=1, framealpha=1)

plt.show()

### Helioprojective Cartesian Coordinates



In [ ]:
# Plot the composite image
fig_hpc = plt.figure(figsize=(10, 10))
fig_hpc.tight_layout(h_pad=-50)
fig_hpc.suptitle(f'Helioprojective Cartesian Coordinates, GOES-{goes}')
ax_hpc = fig_hpc.add_subplot(projection=suvi_map)
suvi_map.plot(axes=ax_hpc, clip_interval=(0.1, 99.9) * u.percent)

chbnd_hpc = chbnd_nc['chbnd_loc_hpc'][:].data[0]

colors = cm.Blues_r(np.linspace(0., 0.3, len(chbnd_hpc)))

for hole, c in zip(chbnd_hpc, colors):
    hole = [*hole, hole[0]]
    hole = np.array(hole, dtype=float)
    hole = np.where(hole == -9999., np.nan, hole)
    chbnd_hpc_sc = SkyCoord([(float(v[0]), float(v[1])) * u.arcsec for v in hole], obstime=date,
                            observer=suvi_map.observer_coordinate, frame=frames.Helioprojective)
    # Transform skycoord object to the suvi sunpy map's coordinate frame
    chbnd_hpc_sc.transform_to(suvi_map.coordinate_frame)

    # Plot flare
    ax_hpc.plot_coord(chbnd_hpc_sc, color=c, marker='o', markersize=2)

# Add legend for features
handles, labels = legend_handles()
plt.legend(handles, labels, loc=1, framealpha=1)

plt.show()

### Helioprojective Cartesian Coordinates



In [ ]:
# Plot the composite image
fig_hcc = plt.figure(figsize=(10, 10))
fig_hcc.tight_layout(h_pad=-50)
fig_hcc.suptitle(f'Heliocentric Cartesian Coordinates, GOES-{goes}')
ax_hcc = fig_hcc.add_subplot(projection=suvi_map)
suvi_map.plot(axes=ax_hcc, clip_interval=(0.1, 99.9) * u.percent)

chbnd_hcc = chbnd_nc['chbnd_loc_hcc'][:].data[0]

colors = cm.PiYG(np.linspace(0., 0.3, len(chbnd_hcc)))

for hole, c in zip(chbnd_hcc, colors):
    hole = [*hole, hole[0]]
    hole = np.array(hole, dtype=float)
    hole = np.where(hole == -9999., np.nan, hole)
    chbnd_hcc_sc = SkyCoord([(float(v[0]), float(v[1]), float(v[2])) * u.AU for v in hole],
                            obstime=date, observer=suvi_map.observer_coordinate, frame=frames.Heliocentric)

    # Plot flare
    ax_hcc.plot_coord(chbnd_hcc_sc, color=c, marker='o', markersize=2)

# Add legend for features
handles, labels = legend_handles()
plt.legend(handles, labels, loc=1, framealpha=1)

plt.show()

### Heliocentric Radial Coordinates



In [ ]:
chbnd_hcr = chbnd_nc['chbnd_loc_hcr'][:].data[0]

# Plot the composite image
fig = plt.figure(figsize=(10, 10))
fig.tight_layout(h_pad=-50)
fig.suptitle(f'Heliocentric Radial Coordinates, GOES-{goes}')
ax = fig.add_subplot(projection=suvi_map)
suvi_map.plot(axes=ax, clip_interval=(0.1, 99.9) * u.percent)
num_points = 100

colors = cm.BuPu(np.linspace(0.85, 1., len(chbnd_hcr)))

for hole, c in zip(chbnd_hcr, colors):
    hole = [*hole, hole[0]]
    hole = np.array(hole, dtype=float)
    hole = np.where(hole == -9999., np.nan, hole)

    # Need to rotate psi by 90 degrees, according to SkyCoord cylindrical specifications
    chbnd_hcr_sc = SkyCoord(
        [(float(v[0]) * u.solRad, float(v[1] + 90.) * u.deg, float(v[2]) * u.solRad) for v in hole],
        representation_type='cylindrical',
        obstime=date, observer=suvi_map.observer_coordinate, frame=frames.Heliocentric)

    # Plot flare
    ax.plot_coord(chbnd_hcr_sc, color=c, marker='o', markersize=2)

# Add legend for features
handles, labels = legend_handles()
plt.legend(handles, labels, loc=1, framealpha=1)

plt.show()